# Travel-time matrices

:::{dropdown} What is a travel time matrix?
:open:
:color: light
:margin: 1 5 0 0

A travel time matrix is a table that shows the travel time between all pairs of
a set of locations in an urban area. The locations represent typical origins and
destinations, such as everyday services and residential homes, or are a complete
set of locations covering the entire area wall-to-wall, such as census polygons
or a regular grid.

A travel time matrix is a key piece of information in transportation research
and planning. It allows us to study how easily people can reach different
destinations, to evaluate the impacts of transport and land use policies, to
analyse accessibility patterns and to examine how accessibility is influenced by
factors such as the quality of public transport systems, street networks, and
land use patterns. Travel time matrices can also be used to identify in which
areas and for which groups of people a city works best and worst. Altogether,
this makes travel time matrices a critical information to help cities become
more equitable and more sustainable, and to foster a good quality of life for
their residents.

Successful recent research that either used or produced travel time matrices
include the work of the Digital Geography Lab at the University of Helsinki
(e.g., {cite:t}`tenkanen_longitudinal_2020`, {cite:t}`salonen_modelling_2013`,
or {cite:t}`jarv_dynamic_2018`), the Mobility Network at the University of
Toronto (e.g., {cite:t}`farber_dynamic_pt_2017`,
{cite:t}`farber_temporal_variablity_2014`), and the Access to Opportunities
Project (AOP) at the Institute for Applied Economic Research - IPEA (e.g.,
{cite:t}`pereira_geographic_2021`, {cite:t}`braga_evaluating_2023`,
{cite:t}`herszenhut_impact_2022`).
:::


## Load a transport network

As briefly visited in [Quickstart](quickstart) and dicussed in detail in [Data
Requirements](data-requirements), fundamentally, two types of input data are
required for computing a travel time matrix:

- a transport network, and
- a set of origins and destinations

In the example below, we first create a
{class}`TransportNetwork<r5py.TransportNetwork>`. To do so, we load an
OpenStreetMap extract of the São Paulo city centre as well as a public transport
schedule in GTFS format covering the same area. Again, we use the [sample data
sets that can be installed separately](../installation/installation.md#sample-data-sets)

In [1]:
import r5py
import r5py.sampledata.sao_paulo

transport_network = r5py.TransportNetwork(
    r5py.sampledata.sao_paulo.osm_pbf,
    [
        r5py.sampledata.sao_paulo.gtfs,
    ]
)

Studies that compare accessibility between different neighbourhoods tend to use
a regular grid of points that covers the study area as origins or destinations.
Recently, hexagonal grids, such as Uber’s [H3 indexing
system](https://h3geo.org/) have gained popularity, as they assure equidistant
neighbourhood relationships (all neighbouring grid cells’ centroids are at the
same distance; in a grid of squares, the diagonal neighbours are roughly 41%
further than the horizontal and vertical ones).

We prepared such a hexagonal grid for São Paulo, and added the counts of
`population`, `jobs`, and `schools` within each cell as separate columns.
The `id` column refers to the H3 address of the grid cells.

In [2]:
import geopandas

hexagon_grid = geopandas.read_file(r5py.sampledata.sao_paulo.hexgrid_gpkg)
hexagon_grid

id  population  jobs  schools  \
0    89a8100c603ffff        1146  1155        0   
1    89a8100c617ffff         700   463        1   
2    89a8100c60fffff         377   257        0   
3    89a8100c607ffff         743   687        0   
4    89a8100c6abffff         601    29        0   
..               ...         ...   ...      ...   
318  89a8100cea7ffff          34  2483        0   
319  89a8100ce23ffff         382   395        1   
320  89a8100ce37ffff          10   202        0   
321  89a8100c8dbffff          19   438        0   
322  89a8100c8cbffff          12  1375        0   

                                              geometry  
0    POLYGON ((336000.312 7392162.721, 336107.079 7...  
1    POLYGON ((335685.425 7392005.022, 335792.187 7...  
2    POLYGON ((336005.719 7392502.350, 336112.488 7...  
3    POLYGON ((335690.825 7392344.644, 335797.590 7...  
4    POLYGON ((335375.940 7392186.943, 335482.700 7...  
..                                                 ...  
318  POLYGON ((330455.500 7397136.529, 330562.237 7...  
319  POLYGON ((331090.629 7397791.927, 331197.377 7...  
320  POLYGON ((330775.717 7397634.124, 330882.461 7...  
321  POLYGON ((330460.813 7397476.324, 330567.552 7...  
322  POLYGON ((330466.126 7397816.132, 330572.867 7...  

[323 rows x 5 columns]

We can use {meth}`explore()<geopandas.GeoDataFrame.explore()>` to plot the
hexagonal grid in a map:

In [3]:
hexagon_grid.explore()

*R5py* expects origins and destinations to be point geometries. For grid cells,
the geometric center point (‘centroid’) is a good approximisation. One can use
{attr}`geopandas.GeoSeries.centroid` to quickly derive a centroid (point)
geometry from a polygon. We will create one data frame for origins, and one for
destinations:

In [4]:
origins = hexagon_grid.copy()
origins["geometry"] = origins.geometry.centroid

In [5]:
destinations = hexagon_grid.copy()
destinations["geometry"] = destinations.geometry.centroid

## Compute a travel time matrix

With this, we have all input data sets needed for computing a travel time
matrix: a transport network, origins, and destinations. We still need to decide
which modes of transport should be used, and the departure time in our analysis.

The modes of transport can be passed as a list of different
{class}`r5py.TransportMode`s (or their {class}`str` equivalent). Meanwhile, the
departure must be a {class}`datetime.datetime`. If you search for public
transport routes, [double-check that the departure date and time is covered by
the input GTFS data set](check-gtfs-files).

In [6]:
import datetime

travel_time_matrix = r5py.TravelTimeMatrixComputer(
    transport_network,
    origins=origins,
    destinations=destinations,
    transport_modes=[r5py.TransportMode.TRANSIT],
    departure=datetime.datetime(2019, 5, 13, 14, 0, 0),
).compute_travel_times()

The output of
{meth}`compute_travel_times()<r5py.TravelTimeMatrixComputer.compute_travel_times()>`
is a table in which each row describes the travel time (`travel_time`) from an
origin (`from_id`), to a destination (`to_id`).

In [7]:
travel_time_matrix

from_id            to_id  travel_time
0       89a8100c603ffff  89a8100c603ffff          0.0
1       89a8100c603ffff  89a8100c617ffff         13.0
2       89a8100c603ffff  89a8100c60fffff          6.0
3       89a8100c603ffff  89a8100c607ffff         11.0
4       89a8100c603ffff  89a8100c6abffff         20.0
...                 ...              ...          ...
104324  89a8100c8cbffff  89a8100cea7ffff         15.0
104325  89a8100c8cbffff  89a8100ce23ffff         15.0
104326  89a8100c8cbffff  89a8100ce37ffff          9.0
104327  89a8100c8cbffff  89a8100c8dbffff          6.0
104328  89a8100c8cbffff  89a8100c8cbffff          0.0

[104329 rows x 3 columns]

In [8]:
import myst_nb

origins_length = len(origins)
destinations_length = len(destinations)
matrix_length = origins_length * destinations_length

myst_nb.glue("origins_length", origins_length, display=False)
myst_nb.glue("destinations_length", destinations_length, display=False)
myst_nb.glue("matrix_length", matrix_length, display=False)

:::{admonition} A note about transit travel times and travel time windows
:class: attention

With transit travel times, individuals can face (sometimes significantly)
different total travel times depending on when they start their journey. For
example, a rider taking a bus that comes every 15 minutes on the 15-minute mark
will face a travel time that is 14 minutes longer if they arrive at the stop at
09:01 versus if they arrive at 09:15.

To account for that, the R5 engine computes a travel time for every minute in a
specified interval, and reports a median (or, with some customization a
percentile other than the median) travel time over that intervale. For example,
if the specified window is 60 minutes long and the `departure` parameter is set
to 09:00, then the reported travel time will be the median of the 60
minute-by-minute travel times between 09:00 and 10:00.

In r5py the default `departure_time_window` (the interval over which to sample)
is set to 10 minutes. This is done to allow for a result that is as close as
possible to a "single" travel time measure.

**Be careful** as choosing very low intervals (or even not-very-low intervals)
can have some adverse effects on the ability of R5 to find a route to a
destination. If you are working with transit schedules that have very low
frequencies (large gaps in time between subsequent vehicles), you may want to
ensure that `departure_time_window` is set significantly higher than these
headway gaps. The reasons for this are quite technical, but you can read more if
you are interested in the discussion on this issue by visiting [this GitHub
issue](https://github.com/r5py/r5py/issues/292).
:::

The {class}`TravelTimeMatrixComputer<r5py.TravelTimeMatrixComputer>` creates an
all-to-all matrix in long format. In other words, the results contain one row
for every combination of origins and destinations. Since we have
{glue:}`origins_length` origins and {glue:}`destinations_length` destinations,
the output travel time matrix is {glue:}`matrix_length` rows long.

Alternatively, and possibly more intuitively, we can display the travel time
matrix table as a matrix in wide format, using {meth}`pandas.DataFrame.pivot()`:

In [9]:
travel_time_matrix.pivot(index="from_id", columns="to_id", values="travel_time")

to_id            89a8100c003ffff  89a8100c007ffff  89a8100c00bffff  \
from_id                                                              
89a8100c003ffff              0.0              9.0              6.0   
89a8100c007ffff              9.0              0.0             11.0   
89a8100c00bffff              6.0             11.0              0.0   
89a8100c00fffff              9.0              7.0              9.0   
89a8100c013ffff              9.0             13.0             15.0   
...                          ...              ...              ...   
89a8100ea4fffff             45.0             37.0             48.0   
89a8100ea53ffff             41.0             36.0             46.0   
89a8100ea5bffff             37.0             31.0             42.0   
89a8100eacbffff             45.0             40.0             51.0   
89a8100eadbffff             53.0             47.0             58.0   

to_id            89a8100c00fffff  89a8100c013ffff  89a8100c017ffff  \
from_id                                                              
89a8100c003ffff              9.0              9.0              6.0   
89a8100c007ffff              7.0             13.0              7.0   
89a8100c00bffff              9.0             15.0             12.0   
89a8100c00fffff              0.0             16.0             10.0   
89a8100c013ffff             16.0              0.0             10.0   
...                          ...              ...              ...   
89a8100ea4fffff             40.0             50.0             43.0   
89a8100ea53ffff             39.0             46.0             38.0   
89a8100ea5bffff             34.0             41.0             34.0   
89a8100eacbffff             43.0             50.0             42.0   
89a8100eadbffff             50.0             57.0             50.0   

to_id            89a8100c01bffff  89a8100c023ffff  89a8100c027ffff  \
from_id                                                              
89a8100c003ffff             10.0             22.0             30.0   
89a8100c007ffff             17.0             13.0             22.0   
89a8100c00bffff             11.0             24.0             31.0   
89a8100c00fffff             17.0             17.0             25.0   
89a8100c013ffff              7.0             26.0             35.0   
...                          ...              ...              ...   
89a8100ea4fffff             53.0             30.0             31.0   
89a8100ea53ffff             49.0             29.0             33.0   
89a8100ea5bffff             45.0             24.0             31.0   
89a8100eacbffff             53.0             33.0             40.0   
89a8100eadbffff             61.0             41.0             47.0   

to_id            89a8100c02bffff  ...  89a8100ddd3ffff  89a8100ddd7ffff  \
from_id                           ...                                     
89a8100c003ffff             24.0  ...             44.0             41.0   
89a8100c007ffff             15.0  ...             36.0             32.0   
89a8100c00bffff             23.0  ...             47.0             43.0   
89a8100c00fffff             17.0  ...             39.0             35.0   
89a8100c013ffff             28.0  ...             49.0             45.0   
...                          ...  ...              ...              ...   
89a8100ea4fffff             28.0  ...             37.0             33.0   
89a8100ea53ffff             30.0  ...             40.0             37.0   
89a8100ea5bffff             26.0  ...             38.0             34.0   
89a8100eacbffff             35.0  ...             48.0             44.0   
89a8100eadbffff             42.0  ...             56.0             52.0   

to_id            89a8100dddbffff  89a8100ea43ffff  89a8100ea4bffff  \
from_id                                                              
89a8100c003ffff             53.0             39.0             42.0   
89a8100c007ffff             45.0             32.0             35.0   
89a8100c00b

***


## Explore results

### Travel times from anywhere to a particular place

Once the travel time matrix is computed, we can use the data to analyse and
visualise different measures of accessibility. For instance, we can filter the
table to show all rows for which the destination is the [Praça da
Sé](https://en.wikipedia.org/wiki/Pra%C3%A7a_da_S%C3%A9), a public square in the
centre of the city. By plotting the travel times in a map, we can quickly assess
how long it takes for residents from different parts of the city to reach this
square by public transport.

For this we first create a copy of the result data frame, filtered to contain
only rows with `to_id` referencing the Praça da Sé. Then, we join this table to
the input hexagonal grid, and drop any records that have `NaN` values, i.e., for
which there was no result. Finally, as we did above, we use the
{meth}`explore()<geopandas.GeoDataFrame.explore()>` to display the values in a
map.

In [10]:
PRAÇA_DA_SÉ = "89a8100c02fffff"

travel_times_to_centre = travel_time_matrix[travel_time_matrix["to_id"] == PRAÇA_DA_SÉ].copy()
travel_times_to_centre = travel_times_to_centre.set_index("from_id")[["travel_time"]]

hexagons_with_travel_time_to_centre = (
    hexagon_grid.set_index("id").join(travel_times_to_centre)
)

hexagons_with_travel_time_to_centre

population  jobs  schools  \
id                                           
89a8100c603ffff        1146  1155        0   
89a8100c617ffff         700   463        1   
89a8100c60fffff         377   257        0   
89a8100c607ffff         743   687        0   
89a8100c6abffff         601    29        0   
...                     ...   ...      ...   
89a8100cea7ffff          34  2483        0   
89a8100ce23ffff         382   395        1   
89a8100ce37ffff          10   202        0   
89a8100c8dbffff          19   438        0   
89a8100c8cbffff          12  1375        0   

                                                          geometry  \
id                                                                   
89a8100c603ffff  POLYGON ((336000.312 7392162.721, 336107.079 7...   
89a8100c617ffff  POLYGON ((335685.425 7392005.022, 335792.187 7...   
89a8100c60fffff  POLYGON ((336005.719 7392502.350, 336112.488 7...   
89a8100c607ffff  POLYGON ((335690.825 7392344.644, 335797.590 7...   
89a8100c6abffff  POLYGON ((335375.940 7392186.943, 335482.700 7...   
...                                                            ...   
89a8100cea7ffff  POLYGON ((330455.500 7397136.529, 330562.237 7...   
89a8100ce23ffff  POLYGON ((331090.629 7397791.927, 331197.377 7...   
89a8100ce37ffff  POLYGON ((330775.717 7397634.124, 330882.461 7...   
89a8100c8dbffff  POLYGON ((330460.813 7397476.324, 330567.552 7...   
89a8100c8cbffff  POLYGON ((330466.126 7397816.132, 330572.867 7...   

                 travel_time  
id                            
89a8100c603ffff         51.0  
89a8100c617ffff         48.0  
89a8100c60fffff         49.0  
89a8100c607ffff         40.0  
89a8100c6abffff         54.0  
...                      ...  
89a8100cea7ffff         44.0  
89a8100ce23ffff         52.0  
89a8100ce37ffff         45.0  
89a8100c8dbffff         44.0  
89a8100c8cbffff         49.0  

[323 rows x 5 columns]

In [11]:
hexagons_with_travel_time_to_centre.explore(
    column="travel_time",
    cmap="YlOrBr",
    tiles="CartoDB.Positron",
)

You can clearly see how travel times do not increase uniformly, but are shorter
along the major transport axes (metro, railways, bus corridors).


***


### Aggregated/average accessibility

Another quick way of getting an understanding of how well different parts of the
city are served by public transport is to aggregate the travel times from or to
each cell over the entire study region. Of course, this creates [edge
effects](https://doi.org/10.1016/B978-008044910-4.00423-5), so in our limited
example, grid cells further outside will have worse over-all accessibility
values. However, if an entire city region, e.g., covering the entire public
transport network, can be captured in one analysis, unwanted artefacts of the
analysis have a smaller impact.

To aggregate travel times, we can use the
{meth}`groupby()<pandas.DataFrame.groupby()>` method of pandas’ data frames, and
one of the different aggregation functions available for the resulting
{class}`pandas.GroupBy` objects. For instance, to show the median travel time
from any cell to any other cell in our grid, we group the results using
`from_id` and {meth}`median()<pandas.GroupBy.median()>`:

In [12]:
median_travel_times = travel_time_matrix.groupby("from_id").median("travel_time")
median_travel_times

travel_time
from_id                     
89a8100c003ffff         42.0
89a8100c007ffff         37.0
89a8100c00bffff         43.0
89a8100c00fffff         38.0
89a8100c013ffff         47.0
...                      ...
89a8100ea4fffff         38.0
89a8100ea53ffff         40.0
89a8100ea5bffff         37.0
89a8100eacbffff         46.0
89a8100eadbffff         54.0

[323 rows x 1 columns]

Again, we can join these median travel times to the hexagonal grid to display a
nice map:

In [13]:
hexagons_with_median_travel_times = (
    hexagon_grid.set_index("id").join(median_travel_times)
)

hexagons_with_median_travel_times.explore(
    column="travel_time", 
    cmap="YlOrBr",
    tiles="CartoDB.Positron",
)

## Bibliography

:::{bibliography}
:filter: docname in docnames
:::